In [1]:
import pandas as pd
from IPython.display import clear_output, Markdown, Math

* read table `test.csv` exported by `whatsapp2csv.sh`

In [2]:
messages = pd.read_csv('test.csv', delimiter='\t')
messages[:20]

date    time                person  \
0   10/18/16  11:18             Lena Carta   
1   10/18/16  11:21            Jonas Weinz   
2   10/18/16  11:21             Lena Carta   
3   10/18/16  11:21          Sonja Vorwerk   
4   10/18/16  11:22             Caner Ucar   
5   10/18/16  11:22    Patrick (Arithmeum)   
6   10/18/16  11:22             Caner Ucar   
7   10/18/16  11:26    Patrick (Arithmeum)   
8   10/18/16  11:34      Simon (Arithmeum)   
9   10/18/16  11:36             Caner Ucar   
10  10/18/16  11:36             Lena Carta   
11  10/18/16  11:37   Jonathan (Arithmeum)   
12  10/18/16  11:37            Jonas Weinz   
13  10/18/16  11:37   Jonathan (Arithmeum)   
14  10/18/16  11:40    Patrick (Arithmeum)   
15  10/18/16  12:02      Thomas Koppelberg   
16  10/18/16  12:12      Kristina Stellwag   
17  10/18/16  12:14      Thomas Koppelberg   
18  10/18/16  12:19      Simon (Arithmeum)   
19  10/18/16  13:36             Caner Ucar   

                                              message  
0                                       Hallo Jonas 😉  
1   Moin moin ;) Vllt. bin ich aber gar nicht Jona...  
2                                                  😱🤕  
3                                                  🙈😂  
4                                                 😂😂😂  
5                                          hallo jeff  
6                       Patrick kein Handy am Empfang  
7                       halts maul und geh ma duschen  
8   Hab dich als Carsten abgespeichert, selber Schuld  
9   Patrick ich hab geduscht mit Kristina und Sonja v  
10                                            ähm....  
11                        Caner benutzt das Damen-Bad  
12  Lüg doch nicht, du tanzt die ganze Zeit aufm T...  
13                                              bääh😱  
14  ja caner so ist das unter frauen..da geht man ...  
15                                        Eeemmm was?  
16             Thomas, du wolltest gestern ja nicht 😜  
17  Ich wollte einiges, aber ich kann mich zurückh...  
18                                            Genau 🙊  
19                                                Sex

* read emoji-data (can be found here: https://www.unicode.org/Public/emoji/11.0/emoji-data.txt) and generate a table file out of it

In [3]:
emoji_blacklist = set([
    0x1F3FB,
    0x1F3FC,
    0x1F3FD,
    0x1F3FE,
    0x1F3FF
])

In [4]:
emoji_data = pd.read_csv('emoji-data.txt', delimiter=';', comment='#', names=["unicode","type"])
emoji_data['type'] = emoji_data['type'].str.strip()
emoji_data = emoji_data[emoji_data['type'] == "Emoji_Presentation"]
emoji_data

unicode                type
228  231A..231B      Emoji_Presentation
229  23E9..23EC      Emoji_Presentation
230  23F0            Emoji_Presentation
231  23F3            Emoji_Presentation
232  25FD..25FE      Emoji_Presentation
233  2614..2615      Emoji_Presentation
234  2648..2653      Emoji_Presentation
235  267F            Emoji_Presentation
236  2693            Emoji_Presentation
237  26A1            Emoji_Presentation
238  26AA..26AB      Emoji_Presentation
239  26BD..26BE      Emoji_Presentation
240  26C4..26C5      Emoji_Presentation
241  26CE            Emoji_Presentation
242  26D4            Emoji_Presentation
243  26EA            Emoji_Presentation
244  26F2..26F3      Emoji_Presentation
245  26F5            Emoji_Presentation
246  26FA            Emoji_Presentation
247  26FD            Emoji_Presentation
248  2705            Emoji_Presentation
249  270A..270B      Emoji_Presentation
250  2728            Emoji_Presentation
251  274C            Emoji_Presentation
252  274E            Emoji_Presentation
253  2753..2755      Emoji_Presentation
254  2757            Emoji_Presentation
255  2795..2797      Emoji_Presentation
256  27B0            Emoji_Presentation
257  27BF            Emoji_Presentation
..              ...                 ...
329  1F6F7..1F6F8    Emoji_Presentation
330  1F6F9           Emoji_Presentation
331  1F910..1F918    Emoji_Presentation
332  1F919..1F91E    Emoji_Presentation
333  1F91F           Emoji_Presentation
334  1F920..1F927    Emoji_Presentation
335  1F928..1F92F    Emoji_Presentation
336  1F930           Emoji_Presentation
337  1F931..1F932    Emoji_Presentation
338  1F933..1F93A    Emoji_Presentation
339  1F93C..1F93E    Emoji_Presentation
340  1F940..1F945    Emoji_Presentation
341  1F947..1F94B    Emoji_Presentation
342  1F94C           Emoji_Presentation
343  1F94D..1F94F    Emoji_Presentation
344  1F950..1F95E    Emoji_Presentation
345  1F95F..1F96B    Emoji_Presentation
346  1F96C..1F970    Emoji_Presentation
347  1F973..1F976    Emoji_Presentation
348  1F97A           Emoji_Presentation
349  1F97C..1F97F    Emoji_Presentation
350  1F980..1F984    Emoji_Presentation
351  1F985..1F991    Emoji_Presentation
352  1F992..1F997    Emoji_Presentation
353  1F998..1F9A2    Emoji_Presentation
354  1F9B0..1F9B9    Emoji_Presentation
355  1F9C0           Emoji_Presentation
356  1F9C1..1F9C2    Emoji_Presentation
357  1F9D0..1F9E6    Emoji_Presentation
358  1F9E7..1F9FF    Emoji_Presentation

[131 rows x 2 columns]

* now build a set out of the unicode types

In [5]:
ord("😀") == int('0x1f600',16)

True

In [6]:
emoji_codes = emoji_data['unicode']
emoji_codes.head()

228    231A..231B    
229    23E9..23EC    
230    23F0          
231    23F3          
232    25FD..25FE    
Name: unicode, dtype: object

* we have to iterate over the whole list and extract all given ranges:

In [7]:
emoji_code_list = []
for entry in emoji_codes:
    # testing whether we have an entry or a range:
    if '.' in entry:
        # range
        a,b = entry.split("..")
        for i in range(int(a,16),int(b,16) +1):
            if i not in emoji_blacklist:
                emoji_code_list.append(i)
    else:
        # single entry
        if i not in emoji_blacklist:
            emoji_code_list.append(int(entry,16))
emoji_code_set = set(emoji_code_list)

In [8]:
# simple test:
print(ord("😀") in emoji_code_set, ord("a") in emoji_code_set)

True False


* expanding column and fill new emojis

In [9]:
messages["emojis"] = None

In [10]:
for i in messages.index:
    emoji_list = []
    to_remove = []
    m = messages.iloc[i]['message']
    for c in str(m):
        if ord(c) in emoji_code_set:
            emoji_list.append(c)
        elif ord(c) in emoji_blacklist:
            to_remove.append(c)
            
    messages.loc[i,'emojis'] = emoji_list
    #remove emiójis from message
    for e in (emoji_list + to_remove):
        m = m.replace(e,"")
    messages.loc[i,'message'] = m


In [11]:
messages[:20]

date    time                person  \
0   10/18/16  11:18             Lena Carta   
1   10/18/16  11:21            Jonas Weinz   
2   10/18/16  11:21             Lena Carta   
3   10/18/16  11:21          Sonja Vorwerk   
4   10/18/16  11:22             Caner Ucar   
5   10/18/16  11:22    Patrick (Arithmeum)   
6   10/18/16  11:22             Caner Ucar   
7   10/18/16  11:26    Patrick (Arithmeum)   
8   10/18/16  11:34      Simon (Arithmeum)   
9   10/18/16  11:36             Caner Ucar   
10  10/18/16  11:36             Lena Carta   
11  10/18/16  11:37   Jonathan (Arithmeum)   
12  10/18/16  11:37            Jonas Weinz   
13  10/18/16  11:37   Jonathan (Arithmeum)   
14  10/18/16  11:40    Patrick (Arithmeum)   
15  10/18/16  12:02      Thomas Koppelberg   
16  10/18/16  12:12      Kristina Stellwag   
17  10/18/16  12:14      Thomas Koppelberg   
18  10/18/16  12:19      Simon (Arithmeum)   
19  10/18/16  13:36             Caner Ucar   

                                              message     emojis  
0                                        Hallo Jonas         [😉]  
1   Moin moin ;) Vllt. bin ich aber gar nicht Jona...        [🤔]  
2                                                         [😱, 🤕]  
3                                                         [🙈, 😂]  
4                                                      [😂, 😂, 😂]  
5                                          hallo jeff         []  
6                       Patrick kein Handy am Empfang         []  
7                       halts maul und geh ma duschen         []  
8   Hab dich als Carsten abgespeichert, selber Schuld         []  
9   Patrick ich hab geduscht mit Kristina und Sonja v         []  
10                                            ähm....         []  
11                        Caner benutzt das Damen-Bad         []  
12  Lüg doch nicht, du tanzt die ganze Zeit aufm T...         []  
13                                               bääh        [😱]  
14  ja caner so ist das unter frauen..da geht man ...         []  
15                                        Eeemmm was?         []  
16              Thomas, du wolltest gestern ja nicht         [😜]  
17  Ich wollte einiges, aber ich kann mich zurückh...         []  
18                                             Genau         [🙊]  
19                                                Sex         []

* get a list only containing messaged with emojis

In [12]:
emoji_messages = messages[[True if len(e) > 0 else False for e in messages['emojis']]]
emoji_messages = emoji_messages[emoji_messages['message'] != ""]

In [13]:
display(emoji_messages)

date    time                  person  \
0     10/18/16  11:18               Lena Carta   
1     10/18/16  11:21              Jonas Weinz   
13    10/18/16  11:37     Jonathan (Arithmeum)   
16    10/18/16  12:12        Kristina Stellwag   
18    10/18/16  12:19        Simon (Arithmeum)   
29    10/18/16  18:38               Lena Carta   
31    10/18/16  18:39               Lena Carta   
32    10/18/16  18:40        Kristina Stellwag   
33    10/18/16  18:42               Lena Carta   
41    10/20/16  12:50       Steffi (Arithmeum)   
44    10/20/16  17:54       Steffi (Arithmeum)   
45    10/20/16  18:08       Steffi (Arithmeum)   
51    10/20/16  20:58            Anna Borutzky   
52    10/20/16  20:58      Patrick (Arithmeum)   
70    10/20/16  22:59     Jonathan (Arithmeum)   
78    10/25/16  01:03               Caner Ucar   
79    10/25/16  01:04      Michael (Arithmeum)   
88    10/25/16  09:02               Lena Carta   
89    10/25/16  09:04     Jonathan (Arithmeum)   
90    10/25/16  10:00               Lena Carta   
93    10/25/16  21:49     Jonathan (Arithmeum)   
94    10/25/16  21:50               Lena Carta   
95    10/25/16  22:13   Konstantin (Arithmeum)   
96    10/25/16  23:28               Caner Ucar   
102   10/27/16  14:43            Sonja Vorwerk   
115   10/28/16  08:32               Lena Carta   
116   10/28/16  09:48               Lena Carta   
117   10/28/16  09:50               Caner Ucar   
118   10/28/16  09:51               Caner Ucar   
121   10/28/16  10:54               Lena Carta   
...        ...     ...                     ...   
8663    5/9/18  17:42              Jonas Weinz   
8665    5/9/18  17:43               Lena Carta   
8675   5/10/18  14:06            Lena Klöckner   
8676   5/10/18  14:07               Caner Ucar   
8677   5/10/18  14:23                Anna Zens   
8678   5/11/18  08:16               Lena Carta   
8679   5/11/18  08:25                Anna Zens   
8680   5/11/18  08:26               Lena Carta   
8681   5/11/18  13:18        Freya (Arithmeum)   
8682   5/12/18  14:53        Freya (Arithmeum)   
8683   5/12/18  15:05            Anna Borutzky   
8689   5/12/18  15:16               Lena Carta   
8692   5/12/18  15:17            Anna Borutzky   
8693   5/12/18  15:17               Caner Ucar   
8695   5/12/18  15:23              Jonas Weinz   
8696   5/12/18  15:23        Freya (Arithmeum)   
8697   5/12/18  15:23               Lena Carta   
8698   5/12/18  15:24        Freya (Arithmeum)   
8699   5/12/18  15:24               Lena Carta   
8700   5/12/18  15:25        Freya (Arithmeum)   
8702   5/12/18  15:25               Lena Carta   
8708   5/12/18  17:56        Freya (Arithmeum)   
8719   5/12/18  20:09               Lena Carta   
8725   5/13/18  17:24        Thomas Koppelberg   
8726   5/14/18  17:00            Sonja Schäfer   
8739   5/14/18  22:40              Jonas Weinz   
8744   5/15/18  17:16               Caner Ucar   
8755   5/17/18  10:43               Lena Carta   
8759   5/17/18  10:43               Lena Carta   
8763   5/17/18  10:45               Lena Carta   

                                                message  \
0                                          Hallo Jonas    
1     Moin moin ;) Vllt. bin ich aber gar nicht Jona...   
13                                                 bääh   
16                Thomas, du wolltest gestern ja nicht    
18                                               Genau    
29                     was du bist morgen nicht da ???    
31    ich dachte diese Woche komplett noch. Aber gut...   
32                Nee das Semester hat doch angefangen    
33    ja hatte ich gerade vergessen . Dabei hatte ic...   
41                                                Klar    
44                 Mein Zug lässt sich auch heute Zeit    
45    Wir fangen doch wahrscheinlich nicht vor halb ...   
51                                 Ist das dein Ernst?    
52       Habs voll vercheckt sry ..gerade erst gemerkt    
70                      

----
## learning part

In [14]:
import numpy as np
import itertools
import sklearn.utils as sku
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer, HashingVectorizer
from sklearn.model_selection import train_test_split

In [15]:
labels=[e[-1] for e in emoji_messages['emojis']]

In [16]:
labels[:10]

['😉', '🤔', '😱', '😜', '🙊', '😔', '😇', '😜', '😶', '👹']

In [17]:
X1, Xt1, y1, yt1 = train_test_split(emoji_messages['message'], labels, test_size=0.1, random_state=4222)

In [18]:
vectorizer = TfidfVectorizer(stop_words='english')
vec_train = vectorizer.fit_transform(X1)
vec_test = vectorizer.transform(Xt1)

In [19]:
from sklearn.ensemble import RandomForestClassifier as RFC
from sklearn.neural_network import MLPClassifier as MLP
from sklearn.naive_bayes import MultinomialNB as MNB
#clf_a = RFC(criterion='entropy', random_state=4222)
clf_a = MLP()
clf_a.fit(vec_train, y1)

/home/jonas/.local/lib/python3.6/site-packages/sklearn/neural_network/multilayer_perceptron.py:564: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  % self.max_iter, ConvergenceWarning)


MLPClassifier(activation='relu', alpha=0.0001, batch_size='auto', beta_1=0.9,
       beta_2=0.999, early_stopping=False, epsilon=1e-08,
       hidden_layer_sizes=(100,), learning_rate='constant',
       learning_rate_init=0.001, max_iter=200, momentum=0.9,
       nesterovs_momentum=True, power_t=0.5, random_state=None,
       shuffle=True, solver='adam', tol=0.0001, validation_fraction=0.1,
       verbose=False, warm_start=False)

In [20]:
pred = clf_a.predict(vectorizer.transform(Xt1))


In [21]:
testlist = pd.DataFrame({'message': Xt1, 'pred': pred, 'trained': yt1})
testlist = pd.merge(testlist, emoji_messages['emojis'].to_frame(), left_index=True, right_index=True)
testlist.to_csv('export.csv')
testlist

message pred trained  \
8663                mehrere Bürostühle hintereinander?     🙈       🤔   
1862                                Ich will auch Essen    😉       😞   
3921                                         2x orange     🙂       🙂   
2222          Man soll auch keine Lernsachen da lassen     😀       😀   
761   Wir können auch gerne wieder bei mir zusammen ...    😇       😉   
3600  Hab den Bus verpasst, den ich eigentlich nehme...    😟       👸   
1794                                      Klaro, gerne     😎       🙂   
861   Sehr gut, Jan! Wenn sich noch jemand melden wü...    😘       😇   
1469              Jaaa aber mein Mitbewohner ist messy     😬       🙊   
6254  Hallöchen  Es hat ein Herr angerufen, der gern...    💁       🙂   
7968                                               Iwo     🤦       😂   
8102                  Keine Ahnung wer da haariger ist     😅       🧐   
6835                                             Danke     😊       😊   
7135               Wurde bestimmt von Big Bang geklaut     🤷       😂   
4556  Ich kann leider nicht, aber arbeiten da nicht ...    😂       😀   
6705           Ist von heute, aber halt 3x in englisch     😇       🙄   
2058                                                 ..    🤦       😅   
2072  Oder fang endlich mal wieder an, was fürs Stud...    😄       😈   
756           Ich hab vom letzten Jahr noch ein Trauma     😂       😆   
5966                     Ist Freitag schon Wochenende?     😍       🤔   
7007  Wenn wir die Klimaanlage im Museum ausschalten...    🤔       🤪   
6968                          Ein Vorbild für uns alle     🤔       🤩   
5665           Kein Problem. Du kannst mich eintragen.     🙂       🙂   
2641  Jonas, du bist gelb markiert! Du kannst keine ...    😉       🙃   
1981                       Da bin ich mir sehr sicher!     😘       😄   
3334          Das wäre auf jeden Fall hilfreich! Danke     😍       🙂   
4447              Ist das Schild denn auch laminiert?!     🤔       😏   
288    da bin ich mal gespannt wie das aussieht, wen...    😂       👍   
4265                     Aber es ist doch gebrochen...     🤔       😢   
7405                                            Partey     🤦       🤪   
...                                                 ...  ...     ...   
4910  Vllt gilt das Schild auch nur für schwarze Hun...    😂       😱   
2047  Ich erprobe mich morgen mit Freya an Addieren ...    🙂       😄   
2650                             Ich kann leider nicht     😕       😕   
299           Das schafft meine Handykamera aber nicht     😂       😉   
2499  also ihr lieben ich arbeite gerade im arithmeu...    😁       😅   
4783                                              danke    😊       💸   
4040                                           Herrlich    🤦       😅   
7553                    babbage, meine Autokerrektur ‍♂    🤔       🤦   
6232                        Bin erst um 9.15Uhr da.....    👍       🔪   
3514               Dankeschön! Dann trage ich dich ein     😘       😊   
3422                                         Schnitzel     😅       😍   
2294                                    Club discreto?     😂       😳   
8218                    auch da bin ich etwas neidisch     🙄       😅   
4463                Möchte jemand was vom Café Roller?     🤧       😂   
8032                       Frohe Ostern an Euch alle...    😊       🐥   
4505  okay, ihr geht eigentlich ganz verantwortungsv...    😊       💁   
4810  Meine Meinung: Wenn das Personal da ist, dann ...    😂       🤷   
5762                         Ein shk ist aber billiger     👵       🙄   
4247  Alle die morgen auf der Arbeit sind: nachher k...    🙈       😂   
2501  ich glaube das wäre eine stilvolle und romanti...    😍       😊   
5278                                Ich kann das machen    💁       ✋   
5747  In der Küche im Kühlschrank steht eine grüne T...    😉       🙂   
7022                                 Dann halt nicht ‍♂    🤷       🤷   
1736                Ich hab absolut keine Ahnung davon     😂       😞   
5909  Wir bekomm

In [22]:
display(clf_a.predict(vectorizer.transform(["Boah Caner"]))[0])

'🙄'

In [23]:
print(chr(0x1F3F))

Ἷ


In [24]:
vec_train[0]

<1x3931 sparse matrix of type '<class 'numpy.float64'>'
	with 2 stored elements in Compressed Sparse Row format>

In [25]:
import ipywidgets as widgets 

out = widgets.Output()

t = widgets.Text()
b = widgets.Button(
    description='get smiley',
    disabled=False,
    button_style='', # 'success', 'info', 'warning', 'danger' or ''
    tooltip='Click me',
    icon='check'
)



def handle_submit(sender):
    with out:
        clear_output()
    with out:
        display(Markdown("# " + str(clf_a.predict(vectorizer.transform([t.value]))[0])))

b.on_click(handle_submit)
    
display(t)
display(widgets.VBox([b, out]))  

Text(value='')

VBox(children=(Button(description='get smiley', icon='check', style=ButtonStyle(), tooltip='Click me'), Output()))